In [243]:
import numpy as np
import pandas as pd
import re
import regex
import nltk
import matplotlib.pyplot as plt
#nltk.download('stopwords')
from nltk.corpus import stopwords

data = pd.read_csv('train.csv', delimiter = ',')

pd.options.display.max_colwidth = 100

display(data.head(4))

id  \
0   0   
1   1   
2   2   
3   3   

                                                                               title  \
0  House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It   
1                            FLYNN: Hillary Clinton, Big Woman on Campus - Breitbart   
2                                                  Why the Truth Might Get You Fired   
3                    15 Civilians Killed In Single US Airstrike Have Been Identified   

               author  \
0       Darrell Lucus   
1     Daniel J. Flynn   
2  Consortiumnews.com   
3     Jessica Purkiss   

                                                                                                  text  \
0  House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It By Darrell Luc...   
1  Ever get the feeling your life circles the roundabout rather than heads in a straight line towar...   
2  Why the Truth Might Get You Fired October 29, 2016 \nThe tension between intelligence analysts a...   
3  Videos 15 Civilians Killed In Single US Airstrike Have Been Identified The rate at which civilia...   

   label  
0      1  
1      0  
2      1  
3      1

In [244]:
print(data.shape)

(20800, 5)


In [245]:
filter = data['text'].str.contains('', regex = True, na = False)

data = data[filter]
print(data.shape)

(20761, 5)


In [246]:
data['total']=data['title']+' '+data['author']+data['text']

In [247]:
data=data.fillna('')

In [248]:
print("before non-latin removal:", data.shape)

before non-latin removal: (20761, 6)


In [249]:
filter = []

for index, row in data.iterrows():
    reg = regex.match(r'[\p{Latin}\p{posix_punct}]+', row['total'])
    if reg == None:
        filter.append(False)
    else:
        filter.append(True)

In [250]:
filter = np.array(filter)

filter

array([ True,  True,  True, ...,  True,  True,  True])

In [251]:
data = data[filter]
print("after non-latin removal:", data.shape)

after non-latin removal: (17835, 6)


In [252]:
pd.options.display.max_colwidth = 100
display(data.head())

id  \
0   0   
1   1   
2   2   
4   4   
5   5   

                                                                                                 title  \
0                    House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It   
1                                              FLYNN: Hillary Clinton, Big Woman on Campus - Breitbart   
2                                                                    Why the Truth Might Get You Fired   
4        Iranian woman jailed for fictional unpublished story about woman stoned to death for adultery   
5  Jackie Mason: Hollywood Would Love Trump if He Bombed North Korea over Lack of Trans Bathrooms (...   

               author  \
0       Darrell Lucus   
1     Daniel J. Flynn   
2  Consortiumnews.com   
4      Howard Portnoy   
5     Daniel Nussbaum   

                                                                                                  text  \
0  House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It By Darrell Luc...   
1  Ever get the feeling your life circles the roundabout rather than heads in a straight line towar...   
2  Why the Truth Might Get You Fired October 29, 2016 \nThe tension between intelligence analysts a...   
4  Print \nAn Iranian woman has been sentenced to six years in prison after Iran’s Revolutionary Gu...   
5  In these trying times, Jackie Mason is the Voice of Reason. [In this week’s exclusive clip for B...   

   label  \
0      1   
1      0   
2      1   
4      1   
5      0   

                                                                                                 total  
0  House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It Darrell LucusH...  
1  FLYNN: Hillary Clinton, Big Woman on Campus - Breitbart Daniel J. FlynnEver get the feeling your...  
2  Why the Truth Might Get You Fired Consortiumnews.comWhy the Truth Might Get You Fired October 29...  
4  Iranian woman jailed for fictional unpublished story about woman stoned to death for adultery Ho...  
5  Jackie Mason: Hollywood Would Love Trump if He Bombed North Korea over Lack of Trans Bathrooms (...

In [253]:
data['text'].replace(regex=True, inplace=True,to_replace='\n', value='')
data.to_csv('newtrain.csv')

txts = data['text'].tolist()

In [254]:
stopWords = set(stopwords.words('english'))

In [264]:
from sklearn.feature_extraction.text import CountVectorizer
vectorizer = CountVectorizer()

# tokenize and build vocab
vectorizer.fit(txts)
vocabulary = vectorizer.vocabulary_
print(vectorizer.vocabulary_)

{'house': 61875, 'dem': 35065, 'aide': 6312, 'we': 140906, 'didn': 36907, 'even': 45432, 'see': 116101, 'comey': 27969, 'letter': 75981, 'until': 136360, 'jason': 68245, 'chaffetz': 24430, 'tweeted': 133869, 'it': 67481, 'by': 21557, 'darrell': 33550, 'lucus': 78247, 'on': 93309, 'october': 92505, '30': 1861, '2016': 1337, 'subscribe': 125194, 'the': 129592, 'stump': 124867, 'in': 64255, 'american': 8053, 'fork': 50169, 'utah': 136944, 'image': 63647, 'courtesy': 31019, 'michael': 83568, 'jolley': 69267, 'available': 12650, 'under': 134990, 'creative': 31423, 'commons': 28175, 'license': 76343, 'with': 142658, 'apologies': 9733, 'to': 130969, 'keith': 71146, 'olbermann': 93036, 'there': 129812, 'is': 67192, 'no': 90509, 'doubt': 39307, 'who': 141912, 'worst': 143246, 'person': 98196, 'world': 143177, 'this': 130039, 'week': 141071, 'fbi': 47645, 'director': 37417, 'james': 68042, 'but': 21419, 'according': 4611, 'democratic': 35195, 'looks': 77741, 'like': 76583, 'also': 7617, 'know': 

In [265]:
temp_dict = dict(vocabulary)
print(len(vocabulary))
for key in temp_dict:
    if key in stopWords:
        del vocabulary[key]

147069


In [266]:
print(vocabulary)

{'house': 61875, 'dem': 35065, 'aide': 6312, 'even': 45432, 'see': 116101, 'comey': 27969, 'letter': 75981, 'jason': 68245, 'chaffetz': 24430, 'tweeted': 133869, 'darrell': 33550, 'lucus': 78247, 'october': 92505, '30': 1861, '2016': 1337, 'subscribe': 125194, 'stump': 124867, 'american': 8053, 'fork': 50169, 'utah': 136944, 'image': 63647, 'courtesy': 31019, 'michael': 83568, 'jolley': 69267, 'available': 12650, 'creative': 31423, 'commons': 28175, 'license': 76343, 'apologies': 9733, 'keith': 71146, 'olbermann': 93036, 'doubt': 39307, 'worst': 143246, 'person': 98196, 'world': 143177, 'week': 141071, 'fbi': 47645, 'director': 37417, 'james': 68042, 'according': 4611, 'democratic': 35195, 'looks': 77741, 'like': 76583, 'also': 7617, 'know': 72527, 'second': 115955, 'well': 141274, 'turns': 133713, 'sent': 116659, 'infamous': 65006, 'announcing': 9017, 'looking': 77738, 'emails': 42518, 'may': 81571, 'related': 108566, 'hillary': 60484, 'clinton': 26847, 'email': 42512, 'server': 11692

In [267]:
print(len(vocabulary))

146924


In [276]:
pd.DataFrame([vocabulary]).to_csv('Vocabulary.csv', sep=',')